In [17]:
import glob
import random
import os
import numpy as np 
from scipy import ndimage as ndi
import matplotlib
import matplotlib.pyplot as plt
import scipy.misc 
import tensorflow as tf
import numpy as np
import scipy.io
import cygan
from tensorflow.keras import layers
import tensorflow_addons as tfa

In [18]:
os.environ["CUDA_VISIBLE_DEVICES"] = "1"

from tensorflow.python.client import device_lib
print(device_lib.list_local_devices())

[name: "/device:CPU:0"
device_type: "CPU"
memory_limit: 268435456
locality {
}
incarnation: 16722925024856114403
, name: "/device:GPU:0"
device_type: "GPU"
memory_limit: 31585705728
locality {
  bus_id: 2
  numa_node: 1
  links {
  }
}
incarnation: 7024868221620273242
physical_device_desc: "device: 0, name: Tesla V100S-PCIE-32GB, pci bus id: 0000:d8:00.0, compute capability: 7.0"
]


In [23]:
#ORAL CANCER 5 fold validation
import os
import cv2

path = '/home/auser04/Oral_cancer/'
can = [cv2.resize(cv2.imread(path + 'cancer/' +s),dsize = (224,224), interpolation=cv2.INTER_CUBIC) for s in os.listdir(path+'cancer')if ".jpg" or ".jpeg"in s.lower()]
nor = [cv2.resize(cv2.imread(path + 'normal/' +s), dsize = (224,224), interpolation=cv2.INTER_CUBIC) for s in os.listdir(path+'normal')if ".jpg"in s.lower()]


can = (np.array(can)-127.5)/127.5
nor = (np.array(nor)-127.5)/127.5
allCAN = np.concatenate((CAN,can,CAN,can),axis=0)
allNOR = np.concatenate((NOR,nor,NOR[0:2],NOR,nor),axis=0)
res_x = np.append(allNOR,allCAN,axis=0)
print(allCAN.shape,allNOR.shape)
#NOR10 CAN38

[[[[-0.89019608 -0.65490196 -0.33333333]
   [-0.8745098  -0.61568627 -0.2627451 ]
   [-0.96078431 -0.65490196 -0.30196078]
   ...
   [-0.39607843 -0.28627451  0.04313725]
   [-0.64705882 -0.44313725 -0.01960784]
   [-0.65490196 -0.51372549 -0.12941176]]

  [[-0.88235294 -0.61568627 -0.27843137]
   [-0.92156863 -0.67058824 -0.33333333]
   [-0.92941176 -0.65490196 -0.30196078]
   ...
   [-0.73333333 -0.49803922 -0.09019608]
   [-0.64705882 -0.38823529 -0.01176471]
   [-0.60784314 -0.39607843 -0.01960784]]

  [[-0.9372549  -0.6627451  -0.34901961]
   [-0.81960784 -0.63137255 -0.30196078]
   [-0.89803922 -0.67058824 -0.38823529]
   ...
   [-0.6627451  -0.41176471 -0.02745098]
   [-0.69411765 -0.35686275 -0.06666667]
   [-0.70196078 -0.49019608 -0.09019608]]

  ...

  [[-0.48235294 -0.44313725 -0.52156863]
   [-0.50588235 -0.4745098  -0.51372549]
   [-0.54509804 -0.52941176 -0.56862745]
   ...
   [-0.55294118 -0.56862745 -0.11372549]
   [-0.64705882 -0.58431373 -0.12156863]
   [-0.70196078 

In [24]:
from __future__ import print_function, division
import keras
from keras.datasets import mnist
from keras.applications import VGG19
from keras.applications import VGG16
from tensorflow.keras.preprocessing import image
from tensorflow.keras.applications.vgg19 import preprocess_input
from tensorflow.keras.layers import Input, Dense, Reshape, Flatten, Dropout, multiply, Add, Concatenate, MaxPool2D
from tensorflow.keras.layers import BatchNormalization, Activation, Embedding, ZeroPadding2D
from tensorflow.keras.layers import LeakyReLU
# from keras_contrib.layers.normalization.instancenormalization import InstanceNormalization
from tensorflow.keras.layers import UpSampling2D, Conv2D, Conv2DTranspose
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.optimizers import Adam, RMSprop
import tensorflow.keras.backend as K
import matplotlib.pyplot as plt
import tensorflow as tf
import numpy as np
K.clear_session()
class GAN():
    def __init__(self):
        self.img_rows = 224
        self.img_cols = 224
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)
        self.latent_dim = 100

#         optimizer = Adam(0.0002, 0.5)
        self.n_critic = 5
        self.clip_value = 0.01
        optimizer = RMSprop(lr=0.00005)
        
        patch = int(self.img_rows / 2**4)
        self.disc_patch = (patch, patch, 1)
        self.gf = 32
        self.df = 64
        
        # Build and compile the discriminator
        self.discriminator_NOR = self.build_discriminator()
        self.discriminator_NOR.compile(loss='mse',
            optimizer=optimizer,
            metrics=['accuracy'])
        
        self.discriminator_CAN = self.build_discriminator()
        self.discriminator_CAN.compile(loss='mse',
            optimizer=optimizer,
            metrics=['accuracy'])
        
        # Build the generator
        self.generator = self.build_encoder()
        print(self.generator.summary())

        
        
        
        z = Input(shape=self.img_shape)
        img_source = Input(shape = self.img_shape)
        img = self.generator(z)

        # For the combined model we will only train the generator
        self.discriminator_CAN.trainable = False
        self.discriminator_NOR.trainable = False
        # The discriminator takes generated images as input and determines validity
        validity_CAN = self.discriminator_CAN(img)
        validity_NOR = self.discriminator_NOR(img)
        
        # The combined model  (stacked generator and discriminator)
        # Trains the generator to fool the discriminator
        #self.combined = Model([z,img_source],[validity,fake_feature])
        self.combined = Model(z,[validity_NOR,validity_CAN])
        self.combined.compile(loss=['mse','mse'],loss_weights=[1,1], optimizer=optimizer)#tf.keras.losses.MeanAbsoluteError
        #keras.utils.plot_model(self.combined, "combined.png", show_shapes=True)

    def wasserstein_loss(self, y_true, y_pred):
        return K.mean(y_true * y_pred)
        
        return encoder
    def build_encoder(self):
        model = cygan.get_resnet_generator(res = 224,name='en')
        load_status = model.load_weights("ae_wgen_N2C")#"ae_wgen_new_cancer")
        encoder = model
        #encoder = Model(inputs = model.input, outputs = model.get_layer('add_8').output)
#         model = keras.models.load_model('/home/auser04/0428_oral.h5')
#         encoder = Model(inputs = model.input, outputs = model.get_layer('activation_4').output)
        
        
        
        return encoder
             

    
    def build_discriminator(self):
      
        def d_layer(layer_input, filters, f_size=7, normalization=False):
            """Discriminator layer"""
            d = Conv2D(filters, kernel_size=f_size, strides=2, padding='same')(layer_input)
            d = LeakyReLU(alpha=0.2)(d)
            if normalization:
                d = tfa.layers.InstanceNormalization(gamma_initializer=cygan.gamma_init)(d)
            return d

        img = Input(shape=self.img_shape)

        d1 = d_layer(img, self.df, normalization=False)
        d2 = d_layer(d1, self.df*2)
        d3 = d_layer(d2, self.df*4)
        d4 = d_layer(d3, self.df*8)
        validity = Conv2D(1, kernel_size=7, strides=1, padding='same')(d4)

        return Model(img, validity)


    def train(self, epochs, batch_size=128, sample_interval=50, thre = 0.5):

        valid = np.ones((batch_size,) + self.disc_patch)
        fake = np.zeros((batch_size,) + self.disc_patch)
        self.encoder = self.build_encoder()
        for i in range(100):
            idx_NOR = np.random.randint(0, NOR.shape[0], batch_size)
            idx_CAN = np.random.randint(0, CAN.shape[0], batch_size)
            N_imgs = NOR[idx_NOR]
            C_imgs = CAN[idx_CAN]
            self.discriminator_NOR.train_on_batch(C_imgs, valid)
            self.discriminator_NOR.train_on_batch(N_imgs, fake)

        for epoch in range(epochs):

            # ---------------------
            #  Train Discriminator
            # ---------------------

            for _ in range(1):
                idx_NOR = np.random.randint(0, NOR.shape[0], batch_size)
                idx_CAN = np.random.randint(0, CAN.shape[0], batch_size)
                N_imgs = NOR[idx_NOR]
                C_imgs = CAN[idx_CAN]
                gen_imgs = self.generator.predict(N_imgs)
                pre_c = self.discriminator_NOR.predict(C_imgs)
                target_c = pre_c
                target_n = pre_c
                for i in range(target_c.shape[1]):
                    for j in range(target_c.shape[2]):
                        if target_c[0][i][j][0] < np.mean(pre_c):
                            target_c[0][i][j][0]=0
                            target_n[0][i][j][0]=1
                        else:
                            target_c[0][i][j][0] = 1
                            target_n[0][i][j][0]=0

                d_loss_real = self.discriminator_CAN.train_on_batch(C_imgs, target_c) 
                d_loss_fake = self.discriminator_CAN.train_on_batch(N_imgs, target_n)
                d_loss_fake = self.discriminator_CAN.train_on_batch(gen_imgs, fake)
                d_loss_NOR = 0.5 * np.add(d_loss_real, d_loss_fake)
                


            # ---------------------
            #  Train Generator
            # ---------------------


            
            g_loss = self.combined.train_on_batch(N_imgs, [0.5*valid,valid])

            # Plot the progress
            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f, G loss: %f]" % (epoch, d_loss_NOR[0], 100*d_loss_NOR[1], g_loss[0], g_loss[1]))

            # If at save interval => save generated image samples
            if epoch % sample_interval == 0:
                self.sample_images(epoch)

    def sample_images(self, epoch):
        r, c = 2, 5
        #noise = np.random.normal(0, 1, (r * c, self.latent_dim))
        idx_NOR = np.random.randint(0, NOR.shape[0], 25)
        idx_CAN = np.random.randint(0, CAN.shape[0], 25)
        N_imgs = NOR[0:10]
        C_imgs = CAN[0:25]

        gen_imgs = self.generator.predict(N_imgs)

        # Rescale images 0 - 1
        gen_imgs = 0.5 * gen_imgs + 0.5

        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt][:,:,::-1].reshape(224,224,3) )
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("/home/auser04/images/%d_0701.png" % epoch)
        plt.close()


if __name__ == '__main__':
    gan = GAN()
    

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d (Reflectio (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 224, 224, 64) 9408        reflection_padding2d[0][0]       
__________________________________________________________________________________________________
instance_normalization (Instanc (None, 224, 224, 64) 128         conv2d[0][0]                     
______________________________________________________________________________________________

Model: "en"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d_20 (Reflec (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d_32 (Conv2D)              (None, 224, 224, 64) 9408        reflection_padding2d_20[0][0]    
__________________________________________________________________________________________________
instance_normalization_23 (Inst (None, 224, 224, 64) 128         conv2d_32[0][0]                  
_________________________________________________________________________________________________

In [26]:
import tensorflow.keras.backend as K
for th in range(0,5):
    K.clear_session()
    gan = GAN()
    thre = 0.8
    NOR = allNOR[th*5:(th+4)*5]
    CAN = allCAN[th*5:(th+12)*5]
    gan.train(epochs=20000, batch_size=1, sample_interval=100,thre = thre)
    gan.generator.save_weights("5fold_%d_20000_N2C" %th)

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d (Reflectio (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d (Conv2D)                 (None, 224, 224, 64) 9408        reflection_padding2d[0][0]       
__________________________________________________________________________________________________
instance_normalization (Instanc (None, 224, 224, 64) 128         conv2d[0][0]                     
______________________________________________________________________________________________

Model: "en"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
en_img_input (InputLayer)       [(None, 224, 224, 3) 0                                            
__________________________________________________________________________________________________
reflection_padding2d_20 (Reflec (None, 230, 230, 3)  0           en_img_input[0][0]               
__________________________________________________________________________________________________
conv2d_32 (Conv2D)              (None, 224, 224, 64) 9408        reflection_padding2d_20[0][0]    
__________________________________________________________________________________________________
instance_normalization_23 (Inst (None, 224, 224, 64) 128         conv2d_32[0][0]                  
_________________________________________________________________________________________________

0 [D loss: 0.153513, acc.: 86.73%] [G loss: 1.095925, G loss: 0.177236]
1 [D loss: 1.230320, acc.: 17.60%] [G loss: 0.724028, G loss: 0.099415]
2 [D loss: 0.116984, acc.: 91.07%] [G loss: 0.937328, G loss: 0.080441]
3 [D loss: 0.278611, acc.: 59.18%] [G loss: 0.726966, G loss: 0.022807]
4 [D loss: 0.527179, acc.: 19.64%] [G loss: 0.578318, G loss: 0.017994]
5 [D loss: 0.194879, acc.: 73.21%] [G loss: 0.651853, G loss: 0.012044]
6 [D loss: 0.401841, acc.: 36.48%] [G loss: 0.680898, G loss: 0.041871]
7 [D loss: 0.342078, acc.: 54.85%] [G loss: 0.721817, G loss: 0.019042]
8 [D loss: 0.616209, acc.: 15.82%] [G loss: 0.728043, G loss: 0.025872]
9 [D loss: 0.406621, acc.: 26.53%] [G loss: 0.687165, G loss: 0.023077]
10 [D loss: 0.285114, acc.: 54.85%] [G loss: 0.679540, G loss: 0.022050]
11 [D loss: 0.593645, acc.: 15.56%] [G loss: 0.604882, G loss: 0.034551]
12 [D loss: 0.206701, acc.: 64.03%] [G loss: 0.644870, G loss: 0.014304]
13 [D loss: 0.068303, acc.: 94.90%] [G loss: 0.813992, G loss

114 [D loss: 0.474765, acc.: 18.11%] [G loss: 0.532685, G loss: 0.024343]
115 [D loss: 0.118843, acc.: 91.33%] [G loss: 0.644423, G loss: 0.010866]
116 [D loss: 0.186305, acc.: 77.04%] [G loss: 0.667236, G loss: 0.018576]
117 [D loss: 0.085561, acc.: 90.56%] [G loss: 0.739324, G loss: 0.012464]
118 [D loss: 0.101460, acc.: 86.73%] [G loss: 0.777141, G loss: 0.014080]
119 [D loss: 0.088599, acc.: 90.82%] [G loss: 0.878176, G loss: 0.043018]
120 [D loss: 0.262639, acc.: 71.17%] [G loss: 0.699971, G loss: 0.015928]
121 [D loss: 0.086454, acc.: 90.82%] [G loss: 0.784095, G loss: 0.011584]
122 [D loss: 0.188912, acc.: 76.79%] [G loss: 0.761469, G loss: 0.012971]
123 [D loss: 0.575617, acc.: 9.95%] [G loss: 0.616420, G loss: 0.009599]
124 [D loss: 0.246312, acc.: 56.12%] [G loss: 0.617706, G loss: 0.041178]
125 [D loss: 0.156810, acc.: 80.10%] [G loss: 0.651727, G loss: 0.019184]
126 [D loss: 0.201746, acc.: 74.74%] [G loss: 0.658617, G loss: 0.054761]
127 [D loss: 0.147918, acc.: 82.91%] [G

225 [D loss: 0.440005, acc.: 10.71%] [G loss: 0.469474, G loss: 0.012225]
226 [D loss: 0.352829, acc.: 39.29%] [G loss: 0.565100, G loss: 0.092314]
227 [D loss: 0.416063, acc.: 11.48%] [G loss: 0.445740, G loss: 0.012382]
228 [D loss: 0.474347, acc.: 7.40%] [G loss: 0.430826, G loss: 0.017729]
229 [D loss: 0.252441, acc.: 59.18%] [G loss: 0.480789, G loss: 0.012122]
230 [D loss: 0.251008, acc.: 57.40%] [G loss: 0.527496, G loss: 0.029118]
231 [D loss: 0.156019, acc.: 81.63%] [G loss: 0.575285, G loss: 0.006140]
232 [D loss: 0.102611, acc.: 89.03%] [G loss: 0.622952, G loss: 0.013076]
233 [D loss: 0.417362, acc.: 31.38%] [G loss: 0.537306, G loss: 0.022896]
234 [D loss: 0.457928, acc.: 10.71%] [G loss: 0.483385, G loss: 0.011361]
235 [D loss: 0.433334, acc.: 21.94%] [G loss: 0.422469, G loss: 0.022972]
236 [D loss: 0.346762, acc.: 25.26%] [G loss: 0.435988, G loss: 0.014269]
237 [D loss: 0.170777, acc.: 74.23%] [G loss: 0.544464, G loss: 0.021931]
238 [D loss: 0.115699, acc.: 91.33%] [G

...

19535 [D loss: 0.037580, acc.: 96.43%] [G loss: 0.773280, G loss: 0.014393]
19536 [D loss: 0.021197, acc.: 99.74%] [G loss: 0.831171, G loss: 0.012590]
19537 [D loss: 0.046423, acc.: 98.21%] [G loss: 0.667155, G loss: 0.014117]
19538 [D loss: 0.035368, acc.: 98.98%] [G loss: 0.678893, G loss: 0.013896]
19539 [D loss: 0.106143, acc.: 86.22%] [G loss: 0.751059, G loss: 0.015049]
19540 [D loss: 0.029388, acc.: 99.23%] [G loss: 0.722184, G loss: 0.011433]
19541 [D loss: 0.016089, acc.: 100.00%] [G loss: 0.858364, G loss: 0.010903]
19542 [D loss: 0.013508, acc.: 100.00%] [G loss: 0.920348, G loss: 0.023217]
19543 [D loss: 0.048949, acc.: 99.23%] [G loss: 0.715967, G loss: 0.010395]
19544 [D loss: 0.035360, acc.: 99.74%] [G loss: 0.739189, G loss: 0.009221]
19545 [D loss: 0.030389, acc.: 98.72%] [G loss: 0.735080, G loss: 0.013946]
19546 [D loss: 0.014951, acc.: 100.00%] [G loss: 0.816377, G loss: 0.015653]
19547 [D loss: 0.014773, acc.: 100.00%] [G loss: 0.886827, G loss: 0.008114]
19548 [D

19644 [D loss: 0.045216, acc.: 99.49%] [G loss: 0.735861, G loss: 0.021600]
19645 [D loss: 0.045419, acc.: 100.00%] [G loss: 0.636933, G loss: 0.009484]
19646 [D loss: 0.058985, acc.: 99.23%] [G loss: 0.701194, G loss: 0.018898]
19647 [D loss: 0.033969, acc.: 97.19%] [G loss: 0.741907, G loss: 0.013639]
19648 [D loss: 0.053876, acc.: 98.98%] [G loss: 0.665901, G loss: 0.007435]
19649 [D loss: 0.025897, acc.: 98.98%] [G loss: 0.762852, G loss: 0.012898]
19650 [D loss: 0.020771, acc.: 98.47%] [G loss: 0.832087, G loss: 0.010011]
19651 [D loss: 0.061719, acc.: 98.98%] [G loss: 0.678010, G loss: 0.011499]
19652 [D loss: 0.017966, acc.: 100.00%] [G loss: 0.774952, G loss: 0.008907]
19653 [D loss: 0.021549, acc.: 100.00%] [G loss: 0.813242, G loss: 0.011253]
19654 [D loss: 0.062269, acc.: 99.23%] [G loss: 0.716801, G loss: 0.007455]
19655 [D loss: 0.030508, acc.: 99.74%] [G loss: 0.745126, G loss: 0.014906]
19656 [D loss: 0.016358, acc.: 100.00%] [G loss: 0.808271, G loss: 0.010679]
19657 [D

19752 [D loss: 0.033095, acc.: 100.00%] [G loss: 0.809293, G loss: 0.012020]
19753 [D loss: 0.009563, acc.: 100.00%] [G loss: 0.931208, G loss: 0.013797]
19754 [D loss: 0.031320, acc.: 99.74%] [G loss: 0.737419, G loss: 0.018071]
19755 [D loss: 0.023453, acc.: 99.49%] [G loss: 0.767622, G loss: 0.011860]
19756 [D loss: 0.038898, acc.: 98.47%] [G loss: 0.748549, G loss: 0.010997]
19757 [D loss: 0.029928, acc.: 100.00%] [G loss: 0.825688, G loss: 0.009684]
19758 [D loss: 0.014288, acc.: 99.74%] [G loss: 0.876870, G loss: 0.010359]
19759 [D loss: 0.022025, acc.: 99.74%] [G loss: 0.857280, G loss: 0.021181]
19760 [D loss: 0.048965, acc.: 97.96%] [G loss: 0.727212, G loss: 0.011019]
19761 [D loss: 0.027439, acc.: 98.21%] [G loss: 0.814249, G loss: 0.007617]
19762 [D loss: 0.013751, acc.: 100.00%] [G loss: 0.856155, G loss: 0.012678]
19763 [D loss: 0.039027, acc.: 98.21%] [G loss: 0.762834, G loss: 0.008333]
19764 [D loss: 0.035865, acc.: 96.43%] [G loss: 0.771786, G loss: 0.011493]
19765 [D

19860 [D loss: 0.015608, acc.: 100.00%] [G loss: 0.833983, G loss: 0.008970]
19861 [D loss: 0.042830, acc.: 99.74%] [G loss: 0.870889, G loss: 0.008548]
19862 [D loss: 0.017494, acc.: 100.00%] [G loss: 0.870866, G loss: 0.010428]
19863 [D loss: 0.019983, acc.: 99.23%] [G loss: 0.819684, G loss: 0.012621]
19864 [D loss: 0.029065, acc.: 98.47%] [G loss: 0.802271, G loss: 0.017045]
19865 [D loss: 0.018416, acc.: 99.49%] [G loss: 0.835592, G loss: 0.016571]
19866 [D loss: 0.009187, acc.: 100.00%] [G loss: 0.939359, G loss: 0.007083]
19867 [D loss: 0.004412, acc.: 100.00%] [G loss: 1.001149, G loss: 0.011666]
19868 [D loss: 0.080192, acc.: 99.23%] [G loss: 0.736858, G loss: 0.008897]
19869 [D loss: 0.048188, acc.: 98.98%] [G loss: 0.752781, G loss: 0.007060]
19870 [D loss: 0.023701, acc.: 100.00%] [G loss: 0.829500, G loss: 0.016181]
19871 [D loss: 0.023461, acc.: 100.00%] [G loss: 0.830076, G loss: 0.010866]
19872 [D loss: 0.034715, acc.: 98.72%] [G loss: 0.774495, G loss: 0.011245]
19873 

19969 [D loss: 0.007490, acc.: 100.00%] [G loss: 0.956657, G loss: 0.016353]
19970 [D loss: 0.063773, acc.: 100.00%] [G loss: 0.680242, G loss: 0.009335]
19971 [D loss: 0.040988, acc.: 99.49%] [G loss: 0.720023, G loss: 0.023289]
19972 [D loss: 0.069312, acc.: 98.98%] [G loss: 0.681533, G loss: 0.019446]
19973 [D loss: 0.019584, acc.: 99.23%] [G loss: 0.798382, G loss: 0.010318]
19974 [D loss: 0.024542, acc.: 100.00%] [G loss: 0.730503, G loss: 0.012199]
19975 [D loss: 0.022093, acc.: 100.00%] [G loss: 0.777022, G loss: 0.007407]
19976 [D loss: 0.011604, acc.: 100.00%] [G loss: 0.851623, G loss: 0.012250]
19977 [D loss: 0.020680, acc.: 100.00%] [G loss: 0.837947, G loss: 0.011108]
19978 [D loss: 0.083047, acc.: 96.94%] [G loss: 0.692162, G loss: 0.017738]
19979 [D loss: 0.043053, acc.: 98.72%] [G loss: 0.717968, G loss: 0.017321]
19980 [D loss: 0.051715, acc.: 99.23%] [G loss: 0.653271, G loss: 0.020939]
19981 [D loss: 0.025101, acc.: 100.00%] [G loss: 0.751372, G loss: 0.008522]
19982